# Power Stats 

Use RestAPI to read power consumption info for cluster nodes and generate usage reports.  this is based on the [pandas time series tutorial by Jennifer Walker](https://www.dataquest.io/blog/tutorial-time-series-analysis-with-pandas/)

In [ ]:
import requests
import pprint
import datetime
import os
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib.dates as mdates

In [ ]:
# https://stackoverflow.com/a/9031848
import warnings
warnings.filterwarnings('ignore')

In [ ]:
plt.rcParams["figure.figsize"] = (20,6)

Set up credentials to query RestAPI. Bright controls access based on the user identity.  The user's cert.pem and cert.key are automatically generated but the cacert.pem needs to be constructed from the  certs returned by the master.

In [ ]:
cert_file='~/.cm/cert.pem'
key_file='~/.cm/cert.key'
ca_file='cacert.pem'

In [ ]:
cert=(os.path.expanduser(cert_file), os.path.expanduser(key_file))

## Gather Cluster Power Data

In [ ]:
startdate = '2021/06/01 00:00:00'
enddate = '2021/10/20 00:00:00'

In [ ]:
displaystart = '2021-06-01'
displaystop = '2021-10-20'

In [ ]:
params = (
    ('start', startdate),
    ('measurable', 'Pwr_Consumption'),
    ('indent', '1'),
)

In [ ]:
if os.path.exists("ipower_data.csv"):
    df = pd.read_csv("power_data.csv")
else:
    response = requests.get('https://master:8081/rest/v1/monitoring/dump', params=params, cert=cert, verify=False)
    df = pd.DataFrame(response.json()["data"])

Simply read the json response into a dataframe for futher parsing.

## Clean Data and Resample

Some of data values report unrealistic power values.  Any reading over 10kW is considered invalid.  

Shouldn't do that until later since it implicitly filters out NaN

In [ ]:
#df = df.loc[df['raw'] <  10000]

In [ ]:
df

Create a datatime type column from the reported sample times.

In [ ]:
df['datetime'] = pd.to_datetime(df.time, format="%Y/%m/%d %H:%M:%S")

In [ ]:
df

Create an index for the hourly 

In [ ]:
hourly_idx=pd.date_range(startdate, enddate, freq='H')

In [ ]:
hourly_idx

In [ ]:
demodf=pd.DataFrame(np.zeros((1,len(hourly_idx))).T, index=hourly_idx, columns=['sum'])

In [ ]:
demodf

In [ ]:
df.entity

In [ ]:
sorted(df.entity.unique())

In [ ]:
debug=False

# prepare data frame to append to, use zeros for default column 
m6_hourly_pwr=pd.DataFrame(np.zeros((1,len(hourly_idx))).T, index=hourly_idx, columns=['sum'])

for num, entity in enumerate(sorted(df.entity.unique())):
    if entity not in ['c0009']:
        node_pwr=df[df.entity==entity].set_index("datetime")
        node_pwr=node_pwr[['raw']].resample('H').mean()
        node_pwr=node_pwr[startdate:enddate].fillna(method="ffill")
        node_pwr=node_pwr[startdate:enddate].fillna(method="bfill")
        if debug:
          print(node_pwr)
          missing = node_pwr['raw'].isnull().sum()
          print("{}: {} missing {}\n".format(num, entity, missing))
        m6_hourly_pwr[entity]= node_pwr[startdate:enddate]


In [ ]:
m6_hourly_pwr

In [ ]:
m6_hourly_pwr.fillna(0)

## Plot Per-node Hourly for Row 5 Rack 1

This is just to see the data for each node in one plot and get a feel for how the nodes behave relative to each other.  Plot nodes in individual subplotes to decern individual behavior of specific nodes. It does give a sense of how the total power adds up. 

Inspect the nodes in the first rack.

Plot help on [shared x-axis](https://stackoverflow.com/a/37738851)
on [correct pandas legend use](https://stackoverflow.com/a/59797261)
and [subplot legend placement](https://stackoverflow.com/a/27017307)

In [ ]:
dftest=m6_hourly_pwr[displaystart:displaystop].fillna(0).iloc[:,1:2]

In [ ]:
type(dftest)

In [ ]:
print(np.__version__)

In [ ]:
!module 

In [ ]:
dftest.info()

In [ ]:
startnode=35
stopnode=71
num_nodes=stopnode-startnode
fig, axes = plt.subplots(num_nodes,1, sharex=True, figsize=(20,30))
for i in range(startnode, startnode+1):
    print(i)
    dftmp=m6_hourly_pwr[displaystart:displaystop].fillna(0).iloc[:,i+1:i+2]
    dftmp.plot(ax=axes[i], legend=True)
    axes[i].legend(loc='lower left')

Overview plot reveals missing power data for a number of nodes.  Inspect one up close.

In [ ]:
select_node="c0022"

In [ ]:
df[df.entity==select_node].set_index("datetime")["2020-09-01":"2020-10-04"]

In [ ]:
m6_hourly_pwr[displaystart:displaystop].iloc[:,3:4]["2020-10-03":"2020-10-04"]

In [ ]:
m6_hourly_pwr[displaystart:displaystop].iloc[:,3:4]["2020-09-28":"2020-10-14"].plot()

In [ ]:
m6_hourly_pwr[displaystart:displaystop].iloc[:,3:4].plot()

In [ ]:
df[df["entity"]=="c0001"]

In [ ]:
df[df["entity"]=="c0001"]["datetime"].max()

## Identify nodes that have missing data

Identify nodes by ones that have NaN values over the past month.

In [ ]:
nan_mask = m6_hourly_pwr[startdate:enddate].isna()

In [ ]:
power_missing = nan_mask[nan_mask].apply(lambda row: row[row == True].index, axis=1)[1]

In [ ]:
print(*power_missing,sep=", ")

In [ ]:
num_nodes=len(power_missing)
fig, axes = plt.subplots(num_nodes,1, sharex=True, figsize=(20,30))
for i, node in enumerate(power_missing):
    m6_hourly_pwr[node].plot(ax=axes[i], legend=True)
    axes[i].legend(loc='lower left')

In [ ]:
node

In [ ]:
df[df["entity"]==node]["datetime"].max()

In [ ]:
lastreport = pd.DataFrame(columns=('node', 'datetime'))

for i, node in enumerate(power_missing):
    lastreport.loc[i] = [node, df[df["entity"]==node]["datetime"].max()]

In [ ]:
lastreport.sort_values(by="datetime") #["datetime"].sort()

In [ ]:
print("{}:\t{}".format(node, df[df["entity"]==node]["datetime"].max()))

## Plot all nodes power

Create overview plot of all nodes to observe meta-patterns.

In [ ]:
num_nodes=len(m6_hourly_pwr.iloc[:,1:].columns)

fig, axes = plt.subplots(num_nodes,1, sharex=True, figsize=(20,num_nodes))
for i, node in enumerate(m6_hourly_pwr.iloc[:,1:].columns):
    if (i == num_nodes):
        break
    m6_hourly_pwr[node][displaystart:displaystop].plot(ax=axes[i], legend=True)
    axes[i].legend(loc='lower left')


In [ ]:
m6_hourly_pwr.iloc[:,133:199].columns

# Plot Power Usage Graph


Pick the start and end date for the plots from the data range selected above. Generate the sum and plot only it's values.

We skip over the first month of collection because it is uncommonly noisy.

In [ ]:
kW = m6_hourly_pwr.iloc[:,133:199][displaystart:displaystop].sum(axis=1)/1000

In [ ]:
ax = kW.plot()
ax.set_ylabel("Power (kW)")
ax.set_title("Cheaha compute and login node hourly power use")

Resample hourly sum to support the seven day average.

In [ ]:
kW_d = kW.resample('D').mean()

In [ ]:
# Compute the centered 7-day rolling mean
# https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.rolling.html
kW_7d = kW_d.rolling(7, center=True).mean()

In [ ]:
# Plot houry, daily, 7-day rolling mean
fig, ax = plt.subplots()
ax.plot(kW, marker='.', markersize=2, color='gray', linestyle='None', label='Hourly Average')
ax.plot(kW_d, color='brown', linewidth=2, label='1-day Average')
ax.plot(kW_7d, color='black', linewidth=4, label='7-day Rolling Average')
label='Trend (7 day Rolling Mean)'
ax.legend()
ax.set_ylabel('Power (kW)')
ax.set_title('Cheaha Trends in Electricity Consumption');

# Save Hourly Power to Dataframe

This makes it easy to use the data in other analysis and learning efforts.

In [ ]:
m6_hourly_pwr.to_pickle("m6_hourly_pwr.gz")

In [ ]:
df.to_pickle("power_stats_raw_df.gz")